In [6]:
!pip install --pre deepchem
!pip install --user --upgrade catboost
!pip install --user --upgrade ipywidgets
!pip install shap
!pip install sklearn
!pip install --upgrade numpy
!jupyter nbextension enable --py widgetsnbextension


[notice] A new release of pip is available: 23.0.1 -> 23.1.1
[notice] To update, run: python3.11 -m pip install --upgrade pip
ERROR: Could not find a version that satisfies the requirement catboost (from versions: 0.1.1)
ERROR: No matching distribution found for catboost

[notice] A new release of pip is available: 23.0.1 -> 23.1.1
[notice] To update, run: python3.11 -m pip install --upgrade pip
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.3/138.3 kB 1.6 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 15.9 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.2/198.2 kB 7.8 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.0.1 -> 23.1.1
[notice] To update, run: python3.11 -m pip install --upgrade pip
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 380.1/380.1 kB 2.7 MB/s eta 0:00:00a 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.tom

We can now import the `deepchem` package to play with.

## Подготовка данных

Датасет содержит `SMILES`, по которым определяются 1024 молекулярных дескрипторов, используя ECPF.

# Алина, тут напиши про ECPF

Суть scaffold — разбить молекулы на группы на основе их молекулярного скелета (фрагмента молекулы, который остается, если удалить все боковые цепочки и заместители), а затем распределить эти группы молекул между обучающей, тестовой и валидационной выборками таким образом, чтобы каждая группа принадлежала только одной выборке. Разделение на основе скелета позволяет гарантировать, что новые молекулы не будут похожи на те, которые модель уже видела в обучающей выборке.

In [1]:
import deepchem as dc
import pandas as pd
from deepchem.molnet.load_function.molnet_loader import TransformerGenerator, _MolnetLoader

from deepchem.data import Dataset
from typing import List, Optional, Tuple, Union
import pandas as pd
import numpy as np
import random
import os
from sklearn.metrics import roc_auc_score, f1_score
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
import catboost
from catboost import *
from catboost import datasets
from catboost import CatBoostClassifier

2023-04-30 21:07:46.305532: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


- `TASKS` - параметры, которы будут предсказываться
- `data_source` - название файла датасета
- `feature_field` - название колонки с smiles
- `data_name` - название датасета

In [2]:
data_dir = "./input"
save_dir = "./output"

In [4]:
task = "ames"
data_acute = "water_acute.csv"
data_long_term = "water_long_term.csv"

df_test_name = data_dir + "/" + task + "/" + task + "_test.csv"
df_train_name = data_dir + "/" + task  + "/"  + task + "_train.csv"
df_valid_name = data_dir + "/" + task  + "/"  + task + "_valid.csv"
df_acute_name = data_dir + "/" + task  + "/"  + data_acute
df_long_term_name = data_dir + "/" + task  + "/"  + data_long_term

task_dir = data_dir + "/" + task
task_save = save_dir + "/" + task
result_ds = save_dir + "/" + task + "/" + "dataset.csv"

In [5]:
acute_df = pd.read_csv(df_acute_name)
long_term_df = pd.read_csv(df_long_term_name)
merge_df = pd.merge(acute_df, long_term_df, on='smiles')
merge_df.to_csv(result_ds)

In [25]:
feature_field="smiles"
TASKS = ['Acute', 'Long-term']

Класс - расширающий `_MolnetLoader` из библиотеки DeepChem. Он используется для загрузки датасета и вычисления молекулярных дескрипторов

In [26]:
class MyLoader(_MolnetLoader):

    def create_dataset(self) -> Dataset:
        loader = dc.data.CSVLoader(tasks=self.tasks,
                                   feature_field=feature_field,
                                   featurizer=self.featurizer)
        return loader.create_dataset(result_ds, shard_size=8192)


def load_tox21(
    featurizer: Union[dc.feat.Featurizer, str] = 'ECFP',
    splitter: Union[dc.splits.Splitter, str, None] = 'scaffold',
    transformers: List[Union[TransformerGenerator, str]] = ['balancing'],
    reload: bool = True,
    data_dir: Optional[str] = task_dir,
    save_dir: Optional[str] = task_save,
    **kwargs
) -> Tuple[List[str], Tuple[Dataset, ...], List[dc.trans.Transformer]]:
    
    loader = MyLoader(featurizer, splitter, transformers, TASKS,
                          data_dir, save_dir, **kwargs)
    return loader.load_dataset(task, reload)

In [27]:
tasks, datasets, transformers = load_tox21()
train_dataset, valid_dataset, test_dataset = datasets

[21:03:15] SMILES Parse Error: syntax error while parsing: undefined
[21:03:15] SMILES Parse Error: Failed parsing SMILES ' undefined' for input: ' undefined'
Failed to featurize datapoint 22, None. Appending empty array
Exception message: Python argument types in
    rdkit.Chem.rdmolfiles.CanonicalRankAtoms(NoneType)
did not match C++ signature:
    CanonicalRankAtoms(RDKit::ROMol mol, bool breakTies=True, bool includeChirality=True, bool includeIsotopes=True)
[21:03:15] SMILES Parse Error: syntax error while parsing: undefined
[21:03:15] SMILES Parse Error: Failed parsing SMILES ' undefined' for input: ' undefined'
Failed to featurize datapoint 23, None. Appending empty array
Exception message: Python argument types in
    rdkit.Chem.rdmolfiles.CanonicalRankAtoms(NoneType)
did not match C++ signature:
    CanonicalRankAtoms(RDKit::ROMol mol, bool breakTies=True, bool includeChirality=True, bool includeIsotopes=True)
[21:03:15] SMILES Parse Error: syntax error while parsing: undefined

KeyError: 'Acute'

In [6]:
df_tr = train_dataset.to_dataframe()
df_t = test_dataset.to_dataframe()
df_v = valid_dataset.to_dataframe()

In [ ]:
x = df_tr.drop(['y1','y2','w1','w2','ids'],axis=1)
y = df_tr[['y1','y2']]
xt = df_t.drop(['y1','y2','w1','w2','ids'],axis=1)
x_smiles = df_t['ids'].to_numpy()
yt = df_t[['y1','y2']]
xv = df_v.drop(['y1','y2','w1','w2','ids'],axis=1)

yv = df_v[['y1','y2']]

In [ ]:
def set_seed(s):
    seed_value= s
    os.environ['PYTHONHASHSEED']=str(seed_value)
    random.seed(seed_value)
    np.random.seed(seed_value)


In [ ]:
set_seed(17)

In [ ]:
def show_history(hist):
    acc = hist.history['AUC']
    val_acc = hist.history['val_AUC']
    epochs = range(1, len(acc) + 1)

    plt.plot(epochs, acc, '-', label='AUC')
    plt.plot(epochs, val_acc, ':', label='Validation Accuracy')
    plt.title('Training and Validation Accuracy')
    plt.xlabel('Epoch')
    plt.ylabel('Accuracy')
    plt.legend(loc='lower right')
    plt.plot()

In [ ]:
cat_features = list(range(x.shape[1]))

In [ ]:
type(cat_features[0])

In [ ]:
modely1 = CatBoostClassifier(
    iterations=100000,
    learning_rate=0.001,
    loss_function='MultiClass',
    # loss_function='CrossEntropy',
    eval_metric='AUC',
    early_stopping_rounds=2000,
    
    # weight=w
        # stratify=True


    # task_type="GPU"
)

modely1.fit(
    x, y['y1'],
    # cat_features=cat_features,
    eval_set=(xv, yv['y1']),
    verbose=False,
    plot=True,

)


In [ ]:
roc_auc_score(yt['y1'],modely1.predict_proba(xt),multi_class='ovr')

In [ ]:
modely2 = CatBoostClassifier(
    iterations=100000,
    learning_rate=0.001,
    loss_function='MultiClass',
    eval_metric='AUC',
    early_stopping_rounds=2000,
    
 
)

modely2.fit(
    x, y['y2'],
    # cat_features=cat_features,
    eval_set=(xv, yv['y2']),
    verbose=False,
    plot=True,

)

In [ ]:
roc_auc_score(yt['y1'],modely2.predict_proba(xt),multi_class='ovr')

In [ ]:
pred1 = modely1.predict(xt).astype('int64')
pred2 = modely2.predict(xt).astype('int64')

In [ ]:
df_savey1 = pd.DataFrame(data={'smiles':list(x_smiles)})
df_savey2 = pd.DataFrame(data={'smiles':list(x_smiles)})
df_savey1['y1']=pred1
df_savey2['y2']=pred2

df_savey1.to_csv('output_classification_y1.csv',index=False)
df_savey2.to_csv('output_classification_y2.csv',index=False)     